In [ ]:
import pandas as pd 
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from gensim.models import LdaMulticore
import gensim
import spacy 
import nltk 
from nltk import ngrams
import re
#from utilities import * 

In [ ]:

#load the cleaned and preprocessed dataset 
ArNews_df_update = pd.read_csv("/Users/AlaAlBinSaleh/Desktop/Desktop/Capstone/ArNews_df_Cleaned.csv", index_col=[0])

In [9]:
def clean_str(text):
    search = ["أ","إ","آ","ة","_","-","/",".","،"," و "," يا ",'"',"ـ","'","ى","\\",'\n', '\t','&quot;','?','؟','!']
    replace = ["ا","ا","ا","ه"," "," ","","",""," و"," يا","","","","ي","",' ', ' ',' ',' ? ',' ؟ ',' ! ']
    
    #remove tashkeel
    p_tashkeel = re.compile(r'[\u0617-\u061A\u064B-\u0652]')
    text = re.sub(p_tashkeel,"", text)
    
    #remove longation
    p_longation = re.compile(r'(.)\1+')
    subst = r"\1\1"
    text = re.sub(p_longation, subst, text)
    
    text = text.replace('وو', 'و')
    text = text.replace('يي', 'ي')
    text = text.replace('اا', 'ا')
    
    for i in range(0, len(search)):
        text = text.replace(search[i], replace[i])
    
    #trim    
    text = text.strip()

    return text

#word embedding

In [8]:

#1)Word Embding using AraVec 
model = gensim.models.Word2Vec.load("full_grams_cbow_100_wiki/full_grams_cbow_100_wiki.mdl")

In [10]:
#test the model vocbulary 
print("We've",len(model.wv.index_to_key),"vocabularies")

We've 662109 vocabularies


In [ ]:
%mkdir spacyModel

mkdir: spacyModel: File exists


In [ ]:
model.wv.save_word2vec_format("./spacyModel/aravec.txt")

In [ ]:
!gzip ./spacyModel/aravec.txt

In [ ]:
#!python3 -m spacy init ar spacy.aravec.model --vectors-loc ./spacyModel/aravec.txt.gz
!python3 -m spacy init vectors ar ./spacyModel/aravec.txt.gz ./spacy.aravec.model
#spacy.aravec.model --vectors-loc ./

ℹ Creating blank nlp object for language 'ar'
[2021-11-12 23:16:03,453] [INFO] Reading vectors from spacyModel/aravec.txt.gz
662109it [01:21, 8129.57it/s]
[2021-11-12 23:17:24,926] [INFO] Loaded vectors from spacyModel/aravec.txt.gz
✔ Successfully converted 662109 vectors
✔ Saved nlp object with vectors to output directory. You can now use
the path to it in your config as the 'vectors' setting in [initialize].
/Users/AlaAlBinSaleh/Desktop/Desktop/Capstone/spacy.aravec.model


In [11]:
nlp = spacy.load("./spacy.aravec.model")

In [12]:
# Define the preprocessing Class
class Preprocessor:
    def __init__(self, tokenizer, **cfg):
        self.tokenizer = tokenizer

    def __call__(self, text):
        preprocessed = clean_str(text)
        return self.tokenizer(preprocessed)

In [14]:
nlp.tokenizer = Preprocessor(nlp.tokenizer)
nlp.tokenizer

In [15]:
#Test the word embedding 
nlp("بيانات").vector

array([ 1.3541306 , -0.47691634, -2.037478  ,  1.7818414 ,  3.2348447 ,
        2.9923422 , -1.6732128 ,  2.8066268 , -0.13688694,  1.7843444 ,
        0.9327977 , -0.9078639 , -1.3284395 , -0.6065882 ,  3.0176415 ,
       -4.276657  ,  1.2542839 ,  0.89644   ,  4.40036   , -3.3811958 ,
        3.0062063 , -1.9969931 ,  2.0136075 ,  0.8734018 ,  5.452243  ,
        1.7340939 ,  1.3925358 , -1.7027333 , -0.56593776, -3.1578138 ,
       -2.6459064 , -1.2861159 ,  2.8269248 , -2.9818544 ,  3.3686252 ,
       -2.1550925 ,  0.562423  , -1.5678904 ,  2.0604756 ,  1.0104055 ,
        0.949106  ,  3.5613863 ,  0.21240458,  0.69437015,  0.9959716 ,
       -1.5333009 ,  1.1857115 , -0.6239423 ,  0.79202735, -3.4440598 ,
        2.4681935 , -0.19734618, -1.057888  ,  2.6490996 , -3.813241  ,
       -6.690389  , -1.9947684 , -0.01682599,  3.6795888 , -1.0036598 ,
       -0.08111735, -4.285988  ,  0.13309926, -3.1279614 , -4.398629  ,
        2.2460012 ,  6.380341  , -1.0859216 ,  1.4137076 ,  1.11

In [16]:
model.wv.most_similar("بيانات")

[('البيانات', 0.8408971428871155),
 ('معلومات', 0.7972483038902283),
 ('قاعده_بيانات', 0.7843179702758789),
 ('حسابات', 0.7556501626968384),
 ('المعلومات', 0.7542430758476257),
 ('قاعده_البيانات', 0.7380597591400146),
 ('للبيانات', 0.7246543169021606),
 ('رسائل_البريد_الالكتروني', 0.7245200276374817),
 ('قواعد_بيانات', 0.7238749861717224),
 ('وبيانات', 0.7214061617851257)]

In [ ]:
model.wv["بيانات"]

array([ 1.3541306 , -0.47691634, -2.037478  ,  1.7818414 ,  3.2348447 ,
        2.9923422 , -1.6732128 ,  2.8066268 , -0.13688694,  1.7843444 ,
        0.9327977 , -0.9078639 , -1.3284395 , -0.6065882 ,  3.0176415 ,
       -4.276657  ,  1.2542839 ,  0.89644   ,  4.40036   , -3.3811958 ,
        3.0062063 , -1.9969931 ,  2.0136075 ,  0.8734018 ,  5.452243  ,
        1.7340939 ,  1.3925358 , -1.7027333 , -0.56593776, -3.1578138 ,
       -2.6459064 , -1.2861159 ,  2.8269248 , -2.9818544 ,  3.3686252 ,
       -2.1550925 ,  0.562423  , -1.5678904 ,  2.0604756 ,  1.0104055 ,
        0.949106  ,  3.5613863 ,  0.21240458,  0.69437015,  0.9959716 ,
       -1.5333009 ,  1.1857115 , -0.6239423 ,  0.79202735, -3.4440598 ,
        2.4681935 , -0.19734618, -1.057888  ,  2.6490996 , -3.813241  ,
       -6.690389  , -1.9947684 , -0.01682599,  3.6795888 , -1.0036598 ,
       -0.08111735, -4.285988  ,  0.13309926, -3.1279614 , -4.398629  ,
        2.2460012 ,  6.380341  , -1.0859216 ,  1.4137076 ,  1.11

In [26]:
textes = ArNews_df_update['content'].apply(clean_str)

In [ ]:
def get_existed_tokens(tokens, n_model):
    return [tok for tok in tokens if tok in n_model.wv]
    
def aravec_sentence_embedding(text, model_path):
    t_model = model
    text_clean = clean_str(text).split(" ")
    text_tokens = get_existed_tokens(text_clean, t_model)
    vec = np.zeros(100)
    for token in text_tokens:
        token_vec = t_model.wv[token]
        vec += token_vec
    return vec

In [ ]:
def test_aravec(text,model_path):
    a = aravec_sentence_embedding(text,model_path)
    #print(a)


In [ ]:
emd = []
content = ArNews_df_update["Detokenize"].values
emd = test_aravec(content.map, "full_grams_cbow_100_wiki/full_grams_cbow_100_wiki.mdl")

TypeError: cannot use a string pattern on a bytes-like object

In [32]:
content = ArNews_df_update["Detokenize"].values

In [38]:
def Word_embedding(text):
    global word_embeddings
    word_embeddings = []
    for line in ArNews_df_update["content"]:
        avgword2vec = None
        counter = 0
        #split into sentences 
        for word in line.split():
            if word in model.wv.key_to_index:
                counter += 1
                # words embedding of sentences 
                if avgword2vec is None:
                    avgword2vec = model.wv[word]
                else:
                    avgword2vec = avgword2vec + model.wv[word]
        if avgword2vec is not None:
            avgword2vec = avgword2vec / counter # normalize sum
            word_embeddings.append(avgword2vec)
    return word_embeddings

In [39]:
vec =  Word_embedding(content)

In [40]:
vec

[array([ 0.87453705,  1.2370524 ,  0.17763883, -0.1330908 , -0.45701677,
         0.6180997 , -0.910552  ,  0.7329447 ,  0.55268484,  0.574311  ,
        -0.0358909 ,  0.00777025,  0.98273724,  0.51916784, -0.21750015,
        -1.2604209 , -0.09120488, -0.69955075,  1.4002815 , -0.25394502,
         0.06780173, -0.7325472 ,  1.7613064 , -0.06151843,  0.5160669 ,
        -0.40610015,  0.49209562,  0.71160376, -1.6124972 , -1.3885264 ,
         0.513775  , -0.13925156, -0.86001533, -0.13886188,  0.11869448,
        -0.94766486, -0.01468437, -0.10511401,  0.4901158 , -0.8520456 ,
        -1.2465945 , -0.5131408 ,  0.2616226 ,  0.53239614, -0.3464062 ,
         0.5500683 ,  0.41371456,  0.6054868 , -0.16161731, -1.0566173 ,
        -0.6920138 , -0.3783681 ,  0.58447486,  0.31891677, -0.20282677,
        -1.0390602 , -0.79443043, -1.3049669 , -0.2536757 ,  0.28979698,
        -0.7594617 , -0.08275422, -0.93872815,  1.5961689 , -0.9116024 ,
         0.19583666,  0.28412965,  1.1071297 ,  1.7

In [ ]:
model.wv.key_to_index

{'بني': 316,
 'المش': 78903,
 'هي_احدي_قري': 223,
 'عزله': 2156,
 'الدير_بمديريه_حيران': 464354,
 'التابعه_لمحافظه_حجه': 7195,
 'بلغ_تعداد': 113,
 'سكانها': 58,
 'نسمه_حسب': 102,
 'تعداد_اليمن_لعام': 192,
 '.': 0,
 'عزله_اسلم_الشام': 48626,
 'بمديريه_اسلم_التابعه': 18900,
 'لمحافظه_حجه': 3880,
 'القرو_هي_احدي': 544266,
 'بمديريه_الشاهل_التابعه': 363788,
 'ذراع': 7831,
 'الرفيع': 20526,
 'عزله_بني_فلاح': 278985,
 'بمديريه_افلح_اليمن': 55080,
 'عزله_بني_سعد': 73092,
 'بمديريه_وشحه_التابعه': 41919,
 'الزاويه': 3161,
 'عزله_شرقي_الخميسين': 205058,
 'بمديريه_خيران_المحرق': 105032,
 'بيت': 578,
 'العقبي': 75292,
 'عزله_حملان_بمديريه': 142129,
 'مدينه': 50,
 'حجه_التابعه_لمحافظه': 37424,
 'حجه': 2817,
 'جبل': 828,
 'عبيد': 4124,
 'عزله_غرب_مستباء': 178022,
 'بمديريه_مستباء_التابعه': 100509,
 'عزله_بني_جل': 84332,
 'بمديريه_قفل_شمر': 73093,
 'الغصه': 464355,
 'عزله_المخلاف_بمديريه': 48627,
 'قفل_شمر_التابعه': 37425,
 'البداح_هي_احدي': 407443,
 'قري_عزله_اسلم': 115807,
 'الشام_بمديريه_اسلم': 20

-----------------------------------------------------------------------

In [64]:
corpus=[]
word=[]

for i in range(len(ArNews_df_update['Detokenize'])):
        word =ArNews_df_update['Detokenize'].iloc[i]
        corpus.append(word)

In [66]:
texts = [[word for word in str(document).lower().split()]for document in corpus]

[['حقق',
  'قوت',
  'جيش',
  'وطن',
  'ولي',
  'يمن',
  'كسب',
  'جدد',
  'ميد',
  'اذ',
  'بسط',
  'يطر',
  'دين',
  'زنجبار',
  'عصم',
  'حفظ',
  'ابن',
  'وقع',
  'شرق',
  'عدن',
  'دفع',
  'يلش',
  'حوث',
  'حلفائ',
  'تبع',
  'رئس',
  'سبق',
  'علي',
  'عبد',
  'الل',
  'صلح',
  'فرر',
  'ﺑﺎﺗﺠﺎﻩ',
  'حفظ',
  'يضء',
  'قدم',
  'قوت',
  'جيش',
  'دعم',
  'شعب',
  'حور',
  'ثني',
  'ربط',
  'بخط',
  'تعز',
  'وقل',
  'عمد',
  'عبد',
  'الل',
  'صبح',
  'شرف',
  'عمل',
  'حرر',
  'عدن',
  'يقد',
  'الآ',
  'عمل',
  'حرر',
  'تعز',
  'قته',
  'بتت',
  'شرف',
  'دين',
  'تعز',
  'وقع',
  'دخل',
  'قرب',
  'أضف',
  'قيد',
  'ركز',
  'جيش',
  'نظم',
  'عدن',
  'درس',
  'خير',
  'تاح',
  'وصل',
  'زحف',
  'صنعاء',
  'صعد',
  'وذل',
  'رفع',
  'قيد',
  'يدن',
  'قرر',
  'قدر',
  'رار',
  'وصل',
  'حرب',
  'قلب',
  'طلب',
  'غضن',
  'كشف',
  'صدر',
  'طلع',
  'ـالشرق',
  'وسط',
  'سعد',
  'دعم',
  'عرب',
  'كسح',
  'كشف',
  'لغم',
  'تصل',
  'دين',
  'عدن',
  'طهر',
  'لغم',
  'وتأ',
  'خطة'

In [70]:
from gensim import corpora
dictionary = corpora.Dictionary(texts)
print(dictionary)


Dictionary(45199 unique tokens: ['أضف', 'ابن', 'اخر', 'اذ', 'اضة']...)


In [71]:
corpus = [dictionary.doc2bow(text) for text in texts]
corpus

[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 2),
  (7, 1),
  (8, 2),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 1),
  (16, 2),
  (17, 3),
  (18, 1),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 3),
  (24, 1),
  (25, 2),
  (26, 2),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 3),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 2),
  (39, 1),
  (40, 3),
  (41, 2),
  (42, 1),
  (43, 1),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 2),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 2),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 1),
  (65, 2),
  (66, 2),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 3),
  (71, 5),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 2),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 2),
  (83, 1),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 1),
  (90, 2),
  (91, 2)

In [72]:
lda = gensim.models.LdaModel(corpus, id2word=dictionary, num_topics=5)

In [74]:
print(lda.print_topics(num_topics=5, num_words=15))

[(0, '0.021*"فرق" + 0.020*"لعب" + 0.013*"ندي" + 0.010*"تحد" + 0.010*"قدم" + 0.009*"درب" + 0.008*"سعد" + 0.007*"دور" + 0.007*"وسم" + 0.006*"جمع" + 0.006*"بطل" + 0.006*"جدد" + 0.006*"عقد" + 0.006*"برا" + 0.006*"نخب"'), (1, '0.016*"عمل" + 0.013*"شرك" + 0.008*"نسب" + 0.008*"رفع" + 0.008*"خدم" + 0.007*"خلل" + 0.007*"سعر" + 0.007*"جمع" + 0.007*"قطع" + 0.007*"دول" + 0.006*"سوق" + 0.006*"بلغ" + 0.006*"سعد" + 0.006*"وزر" + 0.006*"سهم"'), (2, '0.014*"سلم" + 0.011*"سعد" + 0.010*"الل" + 0.009*"يمن" + 0.008*"ملك" + 0.008*"وطن" + 0.008*"جمع" + 0.008*"حمد" + 0.007*"حفظ" + 0.007*"عمل" + 0.007*"امن" + 0.007*"دين" + 0.007*"امر" + 0.006*"رئس" + 0.006*"حوث"'), (3, '0.011*"نظم" + 0.010*"جمع" + 0.010*"دول" + 0.010*"عمل" + 0.008*"حكم" + 0.007*"امر" + 0.007*"رئس" + 0.007*"نطق" + 0.006*"قتل" + 0.006*"بلد" + 0.006*"اير" + 0.006*"دخل" + 0.005*"سور" + 0.005*"وقع" + 0.005*"عرق"'), (4, '0.016*"جمع" + 0.010*"نطق" + 0.009*"عمل" + 0.008*"قدم" + 0.007*"عرض" + 0.007*"سعد" + 0.006*"فعل" + 0.006*"خلل" + 0.005*"حفظ" + 0.00